# TMF String tester  
## Relation between string amplitude and driving frequency
In this experiment the string is driven with an electromagnet with frequency sweep from 18 to 35 hz ascending and descending.  
The amplitude of the string is highest when the driving frequency matches its resonant frequency.  
The resonant frequency of the string can be calculated with this formula:  
$$f_{0}=\frac{v}{\lambda}$$
Where $f_{0}$ is the resonant frequency, $v$ is the wave speed and $\lambda$ is the wavelength. 

In [2]:
import numpy as np
import pandas as pd

import plotly
import plotly.express as px

filenames = ['exp5_18-35hz-1200s.csv', 'exp5_35-18hz-1200s.csv']
titles = ['Frequency vs. Amplitude(15Hz-35Hz)', 'Frequency vs. Amplitude(35Hz-15Hz)']

In [3]:
max_displacement_raw = 0.0058162267839687
min_displacement_raw = 0.0320625610948191

min_displacement_mm = 0
max_displacement_mm = 1

def conv_displacement_to_mm(x):
    return (x - min_displacement_raw) * (max_displacement_mm - min_displacement_mm) / (max_displacement_raw - min_displacement_raw) + min_displacement_mm

Firstly we need to read the measured data.

In [4]:
data = []

# Read data files.
for filename in filenames:
    file = pd.read_csv(filename)
    data.append(file[1:])

Then we need to convert the raw current values to string displacement values. According to the [datasheet](https://www.vishay.com/docs/81147/tcst2103.pdf) the current is in mostly linear relation to the displacement.

In [5]:
for experiment in data:
    for i, value in enumerate(experiment['y_val']):
        experiment['y_val'][i] = conv_displacement_to_mm(value)

/home/martinrobomaze/anaconda3/envs/tf/lib/python3.8/site-packages/pandas/core/indexing.py:691: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value, self.name)
/home/martinrobomaze/.local/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3417: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)


0.9944134078212292 0.9962756052141541


Now we need to process the data for plotting. We are averaging the plotted value from 100 sensor readings.

In [6]:
plot_data = [[], []]

for i, experiment in enumerate(data):
    for j in range(0, len(experiment), 100):
        try:
            plot_data[i].append(
                {
                    'frequency': experiment['frequency'][j], 
                    'displacement_y': np.mean(experiment[j:j+100]['y_val'])
                }
            )
        except Exception:
            pass
    
    plot_data[i] = pd.DataFrame(plot_data[i])


In [7]:
for i in range(len(plot_data)):
    fig = px.line(plot_data[i], x=plot_data[i]['frequency'], y=plot_data[i]['displacement_y'], title=titles[i])
    fig.show()


In [8]:
from plotly import graph_objects as go


trace1 = go.Scatter(
    x=plot_data[0]['frequency'], 
    y=plot_data[0]['displacement_y'],
    mode='lines', 
    name='15-35hz'
)

trace2 = go.Scatter(
    x=plot_data[1]['frequency'], 
    y=plot_data[1]['displacement_y'], 
    mode='lines', 
    name='35-15hz'
)

graph_data = [trace1, trace2]
layout = dict(
    title = 'Frequency vs. Amplitude (1200s)',
    xaxis = dict(title='frequency (Hz)'),
    yaxis = dict(title='Amplitude (mm)')
)

fig = go.Figure(
    data = graph_data,
    layout = layout
)

fig.show()

# Results:
- The amplitude is highest at the string's resonant frequency $f_{0}=27.25673 Hz$.  
- The measurement where the frequency was decreasing has an offset to the second one - this shows the non-linearities of the system.  
- The frequency rises in two peaks - this is probably beacuse a wound core string was used which consists of 2 parts